# Desbalanceamento

Nesta seção o equacionamento realizado considerou a aplicação de uma massa de desbalanço excitando o sitema conforme proposto no livro texto da disciplina, "Rotordynamics Prediction in Engineering, Second Edition", {cite:ts}`lalanne_rotordynamics_1998`.

Foram calculadas as amplitudes de vibração em função da velocidade de rotação

## Importando módulos e configurando o ambiente

In [1]:
'''
    Módulos standard
'''
from collections import namedtuple

'''
    Bibliotecas de terceira parte
'''
import numpy as np

'''
    Biblioteca criada para a realização das análises dinâmicas
    no contexto da disciplina
'''
import rotor_analysis as rd

'''
    Configurando pint.Quantity
'''
Q_ = rd.Q_

## Adicionando assimetria ao modelo

In [2]:
import pint

class Spring():
    def __init__(self, coordinate:pint.Quantity, kxx:float=None, kzz:float=None):
        self.coordinate = coordinate
        if kxx:
            self.kxx = kxx
        else:
            self.kxx = Q_(0, "N/m")
        if kzz:
            self.kzz = kzz
        else:
            self.kzz = Q_(0, "N/m")

## Definindo parâmetros

In [3]:
# Material instances and properties
steel = rd.Material(name='Steel',
                    density=Q_(7800, 'kg/m^3'),
                    young_modulus=Q_(2e11,"Pa"))

# Shaft
L = Q_(0.4, 'm')
shaft = rd.Shaft(outer_radius=Q_(0.01, 'm'),
                 inner_radius=Q_(0.0, 'm'),
                 length=L,
                 material=steel)

# Spring
L2 = 2 * L / 3
kzz = Q_(5e5, "N/m")
spring = Spring(L2, kzz=kzz)

# Disc
disc = rd.Disc(outer_radius=Q_(0.150, 'm'),
               inner_radius=Q_(0.010, 'm'),
               length=Q_(0.030, 'm'),
               material=steel,
               coordinate=L/3)

# Rotor
rotor = rd.Rotor(shaft, disc, spring=spring)
speed_range = np.linspace(0, 9000, 101)

# Unbalance
Unbalance = namedtuple(
    'Unbalance',
    ['mass', 'radius']
)
'''
 Numerical data Reference:
     Rotordynamics Prediction in Engineering, Second Edition, by Michel
     Lalanne and Guy Ferraris, Chapter 2: Monorotors, Subsection 2.1.6, page 17.
'''
unbal = Unbalance(
    mass=Q_(1e-4, 'kg'),
    radius=Q_(0.15, 'm')
)

print('Frequências Naturais @ 0 RPM: ', round(rotor.omega_0[0], 2), ',', round(rotor.omega_0[1], 2))
rotor.plot_Campbell()

Frequências Naturais @ 0 RPM:  52.75 , 46.02


In [4]:
def A1_non_sym(speed, *args):
    '''Function to compute the displacemente aplitude A1 of the unbalanced rotor at
    some speed.
    
    Args:
        speed (float): Rotational speed in RPM.
        args: unbalance named tuple with mass and radius as properties

    Reference:
        Rotordynamics Prediction in Engineering, Second Edition, by Michel
        Lalanne and Guy Ferraris equation 
    '''
    unbalance = args[0]
    k1, k2 = rotor.stiffness
    m = rotor.mass
    spin = speed / 60 * 2 * np.pi
    a = rotor.a
    div = (k1 - m * spin**2) * (k2 - m * spin**2) - a**2 * spin**4
    return (k2 - (m + a) * spin**2) * unbalance.mass.m * unbalance.radius.m * (spin)**2 * rotor.f(rotor.discs[0].coordinate.m) / div

    
def A2_non_sym(speed, *args):
    '''Function to compute the displacemente aplitude A2 of the unbalanced rotor at
    some speed.
    
    Args:
        speed (float): Rotational speed in RPM.
        args: unbalance named tuple with mass and radius as properties

    Reference:
        Rotordynamics Prediction in Engineering, Second Edition, by Michel
        Lalanne and Guy Ferraris equation 
    '''
    unbalance = args[0]
    k1, k2 = rotor.stiffness
    m = rotor.mass
    spin = speed / 60 * 2 * np.pi
    a = rotor.a
    div = (k1 - m * spin**2) * (k2 - m * spin**2) - a**2 * spin**4
    return (k1 - (m + a) * spin**2) * unbalance.mass.m * unbalance.radius.m * (spin)**2 * rotor.f(rotor.discs[0].coordinate.m) / div


In [5]:
# Computing the values
values = []
values_A1 = []
values_A2 = []
for speed in speed_range:
    values_A1.append(abs(A1_non_sym(speed, unbal)))
    values_A2.append(abs(A2_non_sym(speed, unbal)))
    values.append(max(values_A1[-1], values_A2[-1]))

# Generating the Standard Campbell Diagram
campbell_fig = rotor.plot_Campbell()

# Call the function to add the secondary y-axis
rd.add_secondary_yaxis(campbell_fig, values)

## Órbita

Após o cômputo da amplitude da resposta ao desbalanço, plota-se os deslocamentos $q1$ e $q2$ formando-se assim a orbita descrita pelo centro do eixo. No caso abaixo temos a órbita simulando o encoder posicionado em q2 (no topo do eixo), e o desbalanço posicionado na chaveta.

Combinando os gráficos anteriormente gerados, temos:

In [6]:
orbit_plot = rd.interactive_orbit_campbell(campbell_fig,
                                           A1_non_sym,
                                           A2_non_sym,
                                           unbal,
                                           initial_speed=2700)
orbit_plot.show()